In [1]:
import numpy as np 
import pandas as pd 
import plotly.express as px 
import matplotlib.pyplot as plt 
%matplotlib inline 
import seaborn as sns 
import scipy as sp 


# Importing the Data Frame & Data Cleaning/Preprocessing

In [3]:
# df = pd.read_excel("/Users/calebsiow/Documents/MATH 185/Project/Rice_MSC_Dataset.xlsx")
df = pd.read_excel("Rice_MSC_Dataset.xlsx")

In [97]:
df['CLASS'].unique()

array(['Basmati', 'Arborio', 'Jasmine', 'Ipsala', 'Karacadag'],
      dtype=object)

In [98]:
df.dropna(inplace=True)

# Seperate Each Class of Rice 

In [99]:
#subsample 7500 rows of data
#create 5 dataframes for each of the 5 different types of rice
df_rice_1 = df.loc[df['CLASS'] == 'Basmati']
df_rice_2 = df.loc[df['CLASS'] == 'Arborio']
df_rice_3 = df.loc[df['CLASS'] == 'Jasmine']
df_rice_4 = df.loc[df['CLASS'] == 'Ipsala']
df_rice_5 = df.loc[df['CLASS'] == 'Karacadag']


# Create a new data frame containing 2000 random samples from each species of rice 

In [100]:
#use pandas transform to fill missing values with weighted similarity between each row
#create a dataframe with 2000 samples of each type of rice
rice = pd.concat([df_rice_1.sample(n=2000), df_rice_2.sample(n=2000), df_rice_3.sample(n=2000), df_rice_4.sample(n=2000), df_rice_5.sample(n=2000)])

# Seperate Features (X) and Labels (Y), Normalize the features

In [101]:
y = rice.CLASS 
#X is the first 16 columns
X = rice.iloc[:, :16]
og = X
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X = sc.fit_transform(X)
X.shape

(10000, 16)

# Function to Compute PCA

In [102]:
#scipy svds 
from numpy.linalg import svd
Xtilde = X - np.mean(X)
def compute_PCA(Xtilde):
    s = Xtilde.T @ Xtilde 
    U, S, V = np.linalg.svd(s)
    proj = Xtilde @ U
    return proj 
projComp = compute_PCA(Xtilde)



# PCA Visualization (3D)

In [103]:
fig = px.scatter_3d(Xtilde, x=projComp[:, 0], y=projComp[:, 1], z=projComp[:, 2], color=y,
                    title="Rice Classification PCA (3D)", width=1500, height=1200, template='plotly_dark', color_discrete_sequence=px.colors.qualitative.Pastel)
fig.update_traces(marker=dict(
    size=2), selector=dict(mode='markers'))
fig.update_layout(scene=dict(xaxis_title='PCA1',
                  yaxis_title='PCA2', zaxis_title='PCA3'))
fig.show()


# PCA Visualization (2D)

In [104]:
fig = px.scatter(Xtilde, x=projComp[:, 0], y=projComp[:, 1], color=y,
                    title="Rice Classification PCA (2D)", width=1500, height=1000, template='plotly_dark', color_discrete_sequence=px.colors.qualitative.Pastel)
fig.update_traces(marker=dict(size=3), selector=dict(mode='markers'))
fig.update_layout(scene=dict(xaxis_title='PCA1', yaxis_title='PCA2'))
fig.show()


# Function to Compute LDA

In [105]:
#lda 
from scipy.linalg import eigh

Ytilde = projComp

def lda(X, labels):
    n,d = X.shape
    levels = np.unique(labels)
    c = len(levels)
    local_centroids = np.zeros((c+1,d))
    xtilde = np.zeros((n,d))
    group_counts = np.zeros((c,1))
    for i in range(c):
        inds_i = np.flatnonzero(labels == levels[i])
        group_counts[i] = np.sum(inds_i)
        local_centroids[i,:] = np.mean(X[inds_i,:],axis=0)
        xtilde[inds_i,:] = X[inds_i,:]-local_centroids[i,:]
    Sw = xtilde.T @ xtilde
    Sb = np.zeros((d,d))
    for i in range(c):
        Sb += group_counts[i] * np.outer(local_centroids[i,:]-np.mean(X,axis=0),local_centroids[i,:]-np.mean(X,axis=0))
    _, eigenvectors = np.linalg.eigh(np.linalg.pinv(Sw).dot(Sb))
    pc = X.dot(eigenvectors[:,::-1][:,:6])
    return pc, eigenvectors

Zlda, V = lda(Ytilde, y)    

    




# LDA Visualization (3D)

In [106]:
fig2 = px.scatter_3d(Xtilde, x=Zlda[:, 0], y=Zlda[:, 1], z=Zlda[:, 2], color=y,
                     template='plotly_dark', color_discrete_sequence=px.colors.qualitative.Pastel2)
fig2.update_layout(scene=dict(xaxis_title='LDA1',
                   yaxis_title='LDA2', zaxis_title='LDA3'))
fig2.update_layout(width=1500, height=1000)

fig2.update_layout(title='Rice Classification LDA 3D')
fig2.update_traces(marker=dict(size=2), selector=dict(mode='markers'))
fig2.show()


# LDA Visualization (2D)

In [107]:
fig2 = px.scatter(Xtilde, x=Zlda[:, 0], y=Zlda[:, 1], color=y, template='plotly_dark', color_discrete_sequence=px.colors.qualitative.Pastel2)
fig2.update_layout(scene=dict(xaxis_title='LDA1', yaxis_title='LDA2'))
fig2.update_layout(width=1500, height=1000)
fig2.update_layout(title_text='LDA (2D)')
fig2.update_traces(marker=dict(size=4), selector=dict(mode='markers'))
fig2.show()


# NCut Spectral Clustering 

In [108]:
from sklearn.cluster import KMeans
from sklearn.neighbors import NearestNeighbors 

ngh = 12
n = X.shape[0]
#random sample of points 2000
subset = np.random.choice(n, 2000, replace=False)
from sklearn.metrics import pairwise_distances
dist = pairwise_distances(X, X, metric='sqeuclidean')

#The code below is finding the k nearest neighbors of each point in X.
def _knn(k, X):
    neigh = NearestNeighbors(n_neighbors=k+1, metric = 'sqeuclidean').fit(X, X)
    k_neighbors = neigh.kneighbors(X, k+1)
    dist = np.array(k_neighbors[0][:, 1:])
    indices = np.array(k_neighbors[1][:, 1:])
    return dist, indices
knn_dist, knn_ind = _knn(ngh, X[subset,:])
sigma = np.mean(knn_dist[:,-1])
W = np.exp(-dist/(2*sigma**2))
#convert diagonal to 0
np.fill_diagonal(W, 0) 
d = np.sum(W, axis=1)
D = np.diag(np.sum(W, axis=1))
invD = np.diag(np.reciprocal(d))
P = invD @ W 
eigenvalues, V = sp.sparse.linalg.eigsh(P, k=6, which='LM')
index = np.argsort(eigenvalues)[::-1]
eigenvalues = eigenvalues[index]
print("Eigenvalues:", eigenvalues)
V = V[:, index]
spectral = KMeans(n_clusters=5, n_init=10).fit(X, V[:,0:6])
spectral_clusters = spectral.labels_




Eigenvalues: [1.02903213 1.02489745 1.00361643 0.96027677 0.86122983 0.74967172]


# Spectral Clustering Visualization (3D)

In [109]:
fig = px.scatter_3d(X, x=projComp[:, 0], y=projComp[:, 1], z=projComp[:, 2], color=spectral_clusters, hover_name=y, template='plotly_dark', title="Spectral Clustering with first 3 Principal Components", color_discrete_map=y)
fig.update_layout(scene = dict(xaxis_title = 'PCA1', yaxis_title = 'PCA2', zaxis_title = 'PCA3'))
fig.update_layout(width=1500, height=1000)
fig.update_traces(marker=dict(size=2), selector=dict(mode='markers'))
fig.show()

# Spectral Clustering (2D)

In [110]:
fig = px.scatter(x=projComp[:, 0], y=projComp[:, 1], color=spectral_clusters, hover_name=y,
                 template='plotly_dark', title="Spectral Clustering with first 2 Principal Components")
fig.update_layout(scene=dict(xaxis_title='PCA1', yaxis_title='PCA2'))
fig.update_layout(width=1500, height=1000)
fig.update_traces(marker=dict(size=2), selector=dict(mode='markers'))
fig.show()


# Clustering Error

In [111]:
from scipy.optimize import linear_sum_assignment

import sys
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
Y = le.fit_transform(y)
def Hungarian(A):
    _, col_ind = linear_sum_assignment(A)
    return col_ind
def clustering_error(L1, L2):
    '''
    Input: L1 = True Labels 
           L2 = Cluster Labels
    Output: Error Rate
    '''
    L1 = L1.flatten(order='F').astype(float)
    L2 = L2.flatten(order='F').astype(float)
    n = L1.size
    if L1.size != L2.size:
        sys.exit('Size of L1 and L2 must be equal.')
    #unique elements in L1
    Label1 = np.unique(L1)
    #how many unique elements in L1
    nClass1 = Label1.size
    #unique elements in L2
    Label2 = np.unique(L2)
    #how many unique elements in L2
    nClass2 = Label2.size
    #maximum number of clusters
    nClass = max(nClass1, nClass2)

    G = np.zeros((nClass, nClass)).astype(float)
    for i in range(0, nClass2):
        for j in range(0, nClass1):
            G[i, j] = np.sum(np.logical_and(L2 == Label2[i], L1 == Label1[j]))
    #find the optimal permutation
    c = Hungarian(-G)
    #find the permuted matrix
    newL2 = np.zeros(L2.shape)
    #permute the matrix
    for i in range(0, nClass2):
        #find the index of the permuted matrix
        newL2[L2 == Label2[i]] = Label1[c[i]]

    #find the error rate
    return 1 - (np.sum(newL2 == L1))/n


In [112]:

NCut_error = clustering_error(Y, spectral_clusters)
print("The NCut Spectral Clustering Error:", NCut_error)


The NCut Spectral Clustering Error: 0.0655


# Spectral Clustering with Python Scikit Learn Library

In [114]:
from sklearn.cluster import SpectralClustering 
spectralClustering = SpectralClustering(n_clusters=5, affinity='nearest_neighbors').fit(X)
spectral_labels = spectralClustering.labels_



# SC Visualization Sklearn

In [115]:
fig12 = px.scatter_3d(x=projComp[:, 0], y=projComp[:, 1], z=projComp[:, 2], color=spectral_labels, hover_name=y,
                      template='plotly_dark', title="Spectral Clustering with first 3 Principal Components")
fig12.update_layout(scene=dict(xaxis_title='PCA1',
                    yaxis_title='PCA2', zaxis_title='PCA3'))
fig12.update_layout(width=1500, height=1000)
fig12.update_traces(marker=dict(size=2), selector=dict(mode='markers'))
fig12.show()


In [116]:
fig6 = px.scatter(df, x=projComp[:, 0], y=projComp[:, 1], color = spectral_labels, hover_name = y, template='plotly_dark', title="Spectral Clustering with first 2 Principal Components")
fig6.update_layout(xaxis_title = 'PCA1', yaxis_title = 'PCA2')
fig6.update_layout(width=1500, height=1000)
fig6.update_traces(marker=dict(size=3), selector=dict(mode='markers'))
fig6.show()

# Spectral Clustering Error with Sklearn

In [117]:
spectral_error = clustering_error(Y, spectral_labels)
print("the spectral clustering error is:", round(spectral_error,4))

the spectral clustering error is: 0.0623


# Visualization of Actual Clusters 

In [118]:
#actual clusters
fig7 = px.scatter_3d(x=projComp[:, 0], y=projComp[:, 1], z= projComp[:,2],color=y,
                    template='plotly_dark', title="Actual Clusters with first 3 Principal Components")
fig7.update_layout(scene = dict(xaxis_title = 'PCA1', yaxis_title = 'PCA2', zaxis_title = 'PCA3'))
fig7.update_layout(width=1500, height=1000)
fig7.update_traces(marker=dict(size=2), selector=dict(mode='markers'))
fig7.show()

In [119]:
#actual clusters
fig8 = px.scatter(x=projComp[:, 0], y=projComp[:, 1], color=y,
                    template='plotly_dark', title="Actual Clusters with first 2 Principal Components")
fig8.update_layout(scene = dict(xaxis_title = 'PCA1', yaxis_title = 'PCA2'))
fig8.update_layout(width=1500, height=1000)
fig8.update_traces(marker=dict(size=3), selector=dict(mode='markers'))
fig8.show()